## RNN


### Installation of packages


In [1]:
%pip install torch
%pip install torchtext
%pip install datasets
%pip install pandas
%pip install scikit-learn

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


### Importing libraries


In [18]:
from collections import Counter
import torch
import pandas as pd
from torchtext.vocab import vocab
from sklearn.model_selection import train_test_split
from tqdm.notebook import tqdm

### Read datasets


In [3]:
def read_data():
    train_dataset = pd.read_csv(
        "train/train.tsv.xz", compression="xz", sep="\t", names=["Label", "Text"]
    )
    dev_0_dataset = pd.read_csv("dev-0/in.tsv", sep="\t", names=["Text"])
    dev_0_labels = pd.read_csv("dev-0/expected.tsv", sep="\t", names=["Label"])
    test_A_dataset = pd.read_csv("test-A/in.tsv", sep="\t", names=["Text"])

    return train_dataset, dev_0_dataset, dev_0_labels, test_A_dataset

In [4]:
train_dataset, dev_0_dataset, dev_0_labels, test_A_dataset = read_data()

### Split the training data into training and validation sets


In [5]:
train_texts, val_texts, train_labels, val_labels = train_test_split(
    train_dataset["Text"], train_dataset["Label"], test_size=0.1, random_state=42
)

In [6]:
train_dataset = pd.DataFrame({"Text": train_texts, "Label": train_labels})
val_dataset = pd.DataFrame({"Text": val_texts, "Label": val_labels})

### Tokenize the text and labels


In [7]:
train_dataset["tokenized_text"] = train_dataset["Text"].apply(lambda x: x.split())
train_dataset["tokenized_labels"] = train_dataset["Label"].apply(lambda x: x.split())

In [8]:
val_dataset["tokenized_text"] = val_dataset["Text"].apply(lambda x: x.split())
val_dataset["tokenized_labels"] = val_dataset["Label"].apply(lambda x: x.split())

In [9]:
dev_0_dataset["tokenized_text"] = dev_0_dataset["Text"].apply(lambda x: x.split())
dev_0_dataset["tokenized_labels"] = dev_0_labels["Label"].apply(lambda x: x.split())

In [10]:
test_A_dataset["tokenized_text"] = test_A_dataset["Text"].apply(lambda x: x.split())

### Create a vocab object which maps tokens to indices


In [11]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [12]:
v = build_vocab(train_dataset["tokenized_text"])

### Map indices to tokens


In [13]:
itos = v.get_itos()

### Number of tokens in the vocabulary


In [14]:
len(itos)

22154

### Index of the 'rejects' token


In [15]:
v["rejects"]

9086

### Index of the '\<unk\>' token


In [16]:
v["<unk>"]

0

### Set the default index to the unknown token


In [17]:
v.set_default_index(v["<unk>"])

### Use cuda if available


In [18]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Vectorize the data


In [19]:
def data_process(dt):
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
            device=device,
        )
        for document in dt
    ]

In [20]:
train_tokens_ids = data_process(train_dataset["tokenized_text"])
val_tokens_ids = data_process(val_dataset["tokenized_text"])
dev_0_tokens_ids = data_process(dev_0_dataset["tokenized_text"])
test_A_tokens_ids = data_process(test_A_dataset["tokenized_text"])

### Create a mapping from label to index


In [21]:
labels = ["O", "B-PER", "I-PER", "B-ORG", "I-ORG", "B-LOC", "I-LOC", "B-MISC", "I-MISC"]

label_to_index = {label: idx for idx, label in enumerate(labels)}

### Vectorize the labels (NER)


In [22]:
def labels_process(dt, label_to_index):
    return [
        torch.tensor(
            [0] + [label_to_index[label] for label in document] + [0],
            dtype=torch.long,
            device=device,
        )
        for document in dt
    ]

In [23]:
train_labels = labels_process(train_dataset["tokenized_labels"], label_to_index)
val_labels = labels_process(val_dataset["tokenized_labels"], label_to_index)
dev_0_labels = labels_process(dev_0_dataset["tokenized_labels"], label_to_index)

### Function for evaluation (returns precision, recall, and F1 score)


In [24]:
def get_scores(y_true, y_pred):
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

### Calculate the number of unique tags


In [25]:
all_label_indices = [
    label_to_index[label]
    for document in train_dataset["tokenized_labels"]
    for label in document
]

num_tags = max(all_label_indices) + 1

print(num_tags)

9


### Implementation of a recurrent neural network LSTM


In [26]:
class LSTM(torch.nn.Module):

    def __init__(self, vocab_size, embedding_dim, hidden_dim, num_layers, num_tags):
        super(LSTM, self).__init__()
        self.embedding = torch.nn.Embedding(vocab_size, embedding_dim)
        self.rec = torch.nn.LSTM(
            embedding_dim, hidden_dim, num_layers, batch_first=True, bidirectional=True
        )
        self.fc1 = torch.nn.Linear(hidden_dim * 2, num_tags)

    def forward(self, x):
        embedding = torch.relu(self.embedding(x))
        lstm_output, _ = self.rec(embedding)
        out_weights = self.fc1(lstm_output)
        return out_weights

### Initialize the LSTM model


In [27]:
lstm = LSTM(len(v.get_itos()), 100, 100, 1, num_tags).to(device)

### Define the loss function


In [28]:
criterion = torch.nn.CrossEntropyLoss()

### Define the optimizer


In [29]:
optimizer = torch.optim.Adam(lstm.parameters())

### Function for model evaluation


In [30]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].cpu().numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.cpu().numpy())

    return get_scores(Y_true, Y_pred)

### Function for returning the predictions labels


In [31]:
def pred_labels(dataset_tokens, model, label_to_index):
    Y_pred = []
    inv_label_to_index = {
        v: k for k, v in label_to_index.items()
    }  # Create the inverse mapping

    for i in tqdm(range(len(dataset_tokens))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        predicted_labels = [inv_label_to_index[label.item()] for label in Y_batch_pred]
        predicted_labels = predicted_labels[1:-1]
        Y_pred.append(" ".join(predicted_labels))

    return Y_pred

### Training


In [32]:
NUM_EPOCHS = 20

In [33]:
for i in range(NUM_EPOCHS):
    lstm.train()
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()
    print(eval_model(val_tokens_ids, val_labels, lstm))

  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.6839857651245551, 0.27638769053782, 0.3936911102007374)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

...

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8210254756530152, 0.73224043715847, 0.7740954697476436)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8173884938590821, 0.727351164797239, 0.7697458529904124)


In [34]:
eval_model(val_tokens_ids, val_labels, lstm)

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8173884938590821, 0.727351164797239, 0.7697458529904124)

In [35]:
eval_model(dev_0_tokens_ids, dev_0_labels, lstm)

  0%|          | 0/215 [00:00<?, ?it/s]

(0.8368401624215578, 0.7924726171055698, 0.8140523071398648)

In [36]:
dev_0_predictons = pred_labels(dev_0_tokens_ids, lstm, label_to_index)
dev_0_predictons = pd.DataFrame(dev_0_predictons, columns=["Label"])
dev_0_predictons.to_csv("dev-0/out.tsv", index=False, header=False)

  0%|          | 0/215 [00:00<?, ?it/s]

In [37]:
test_A_predictions = pred_labels(test_A_tokens_ids, lstm, label_to_index)
test_A_predictions = pd.DataFrame(test_A_predictions, columns=["Label"])
test_A_predictions.to_csv("test-A/out.tsv", index=False, header=False)

  0%|          | 0/230 [00:00<?, ?it/s]

## Correct labels


In [19]:
def correct_labels(input_file, output_file):
    df = pd.read_csv(input_file, sep="\t", names=["Text"])

    corrected_lines = []

    for line in df["Text"]:
        tokens = line.split(" ")
        corrected_tokens = []
        previous_token = "O"

        for token in tokens:
            if (
                token == "I-ORG"
                and previous_token != "B-ORG"
                and previous_token != "I-ORG"
            ):
                corrected_tokens.append("B-ORG")
            elif (
                token == "I-PER"
                and previous_token != "B-PER"
                and previous_token != "I-PER"
            ):
                corrected_tokens.append("B-PER")
            elif (
                token == "I-LOC"
                and previous_token != "B-LOC"
                and previous_token != "I-LOC"
            ):
                corrected_tokens.append("B-LOC")
            elif (
                token == "I-MISC"
                and previous_token != "B-MISC"
                and previous_token != "I-MISC"
            ):
                corrected_tokens.append("B-MISC")
            else:
                corrected_tokens.append(token)

            previous_token = token

        corrected_line = " ".join(corrected_tokens)
        corrected_lines.append(corrected_line)

    df["Text"] = corrected_lines
    df.to_csv(output_file, sep="\t", index=False, header=False)

In [21]:
correct_labels("dev-0/out.tsv", "dev-0/out.tsv")
correct_labels("test-A/out.tsv", "test-A/out.tsv")